# Atmospheric model

## Documentation




***
From the start  >
### 1. Defining the constants

In [1]:
#CONSTANTS

G=6.6743*10**-11 #Gravitational constat
Mz=5.972*10**24 #Earth's mass
Rz=6371 #Earth's radius [km]
secs=24*60*60 #Number of secs in one day

q=1.602176634*10**-19 #elemental charge
go=9.81 #gravitational acceleration
avogadr=6.02214076*10**23

#Values of solar flux min/avgerage/max
solar_min=66.89
solar_max=166.01
solar_avg=92.109


***
### 2. User's Input


 - Engine parameters
     - Inlet capture efficiency: __$\eta$<sub>z</sub>__ [0-1]
     - Inlet ionization efficiency: __$\eta$<sub>i</sub>__ [0-1]  
     - Grid voltage: __V__ [V]
     - Grid area: __Ag__ [m<sup>2</sup>]
     - Inlet area: __Ainlet__ [m<sup>2</sup>]
     - Grid transparency coefficient: __Tg__ [0-1]
     - Drag coefficient: __Cd__ [-]
     - Thrust-to-Power ratio: __TPratio__ [mN/W]
<p>&nbsp;</p> 
 - Spacecraft parameters
     - Spacecraft mass: __m__ [kg]
     - Ram area of a spacecraft
         - Classic = 1 -> (different cubesats): __U3-U27__ [m<sup>2</sup>]
         - Classic = 0 -> Custom value __Area__ [m<sup>2</sup>]
<p>&nbsp;</p>        
 - Orbit definition
     - Initial altitude: __initAlt__ [km]
     - Inclination: __incl__ [°]
<p>&nbsp;</p>        
 - Graph parameters
     - Maximum altitude of orbit for graph plotting: __maxalt__ [km]
     - Minimum altitude of orbit for graph plotting: __minalt__ [km]
     - Altitude step in graphs: __intval__ [km]
<p>&nbsp;</p>      
 - Atmospheric model
     - __Year, Month, Day, Hour, Minute, Seconds, Latitude, Longitude, Solar activity *f107*, Geomagnetic index *ap*, Local solar time *lst*__


In [2]:
#INPUT

#Engine
eta_z=0.9 #capture efficiency
eta_i=0.1 #ionization efficiency
V=1500 #Grid Voltage [V]
Ag=0.031416 #GRID AREA [m2]
Ainlet=0.0707 #inlet area 15 cm radius [m2]
#Ainlet=0.19635 #Inlet area 25 cm radius [m2]
Tg=0.8 #grid Transparency
Cd=2.2 #drag coefficient
TPratio=0.01 #Thrust-to-Power ratio [mN/W]

#Spacecraft
m=20 #spacecraft mass [kg]
Area=0.03 #Ram Ar size [m2]
Ar_classic = 0 #for values of U3-U27 cubesats
               #else set to 0 and ram are manualy

if Ar_classic == 1:
    U3=0.01+Ainlet
    U6=0.02+Ainlet
    U8=0.04+Ainlet
    U27=0.09+Ainlet
    
    
    Ar=[U3,U6,U8,U27]
else:
    Ar=[Area+Ainlet] #set ram area manualy !!
    
#Orbit
initAlt=400 #[km]


#Min and max orbit altitude [km]
maxalt=1000
minalt=0
intval=5



#NMRLSISE00
#==========
#Time of the year
year=1993
month=11
day=5
hour=10
mins=0
sec=0

#Position
lat=50 #Latitude
log=50 #Longitude

#Solar activity
f107=solar_avg #previous day
f107a=solar_avg #present
ap=4 #geomagnetic index
lst=16 #local solar time

***
### 3. Initialization of functions

 - Calculation of orbit velocities
 - Molecular mass and exhaust velocities for different molecules
 - NRLMSISE-00 atmospheric model
 - Calculation of Density
 - Calculation of Beam current and Thrust
 - Calculation of Drag

In [3]:
#imports

import csv
import math
import numpy as np
from datetime import datetime
from nrlmsise00 import msise_model
import matplotlib.pyplot as plt
from matplotlib.widgets import Slider, Button, RadioButtons
%matplotlib widget

#Orbit velocity
  

def getnums(s, e,i):
    return list(range(s, e,i))

orbit=getnums(minalt, maxalt,intval)

v_orbit=[]
for rows in orbit:
    v_orbit.append(math.sqrt(G*Mz/(Rz+rows)/1000)) #vorbit=sqrt(G*Mz/h)
    
#Elements mass

O=16*10**-3
O2=32*10**-3
N2=28.01*10**-3
He=4*10**-3
H=1.01*10**-3

elements=[O,O2,N2,He,H]

#Molecular mass

mol_mass=[]
for element in elements:

    mol_mass.append(element/avogadr)


#Exhaust velocity
v_ex=[]
for element in mol_mass:
    v_ex.append(math.sqrt(2*q*V/element)) #vexhaust=sqrt(2*q*V/mi)
    
    
    
    
#Atmosphere model NRLMSISE

#datetime(year,month,day,hours,min,sec), altitude, latitude, longitude, f107A, f107-previous day, ap-geomagnetic index, lst-local solar time
#output = [density[temperature]] ----> [He, O, N2, O2, Ar, TOTAL MASS, H, N, Anomalous oxygen, [Exhospheric temperature, Temperature at altitude]]
#msise_model(datetime(2009, 11, 20, 22, 58, 20), 400, 60, -70, 150, 150, 4, lst=16)
#msise_model(datetime(year,month,day,hour,mins,sec), alt,log,lat,f107a,f107,ap,lst=lst)


def get_model(f107):

#Poradi co potrebuji: O[1], N2[2], O2[3], He[0], H[6]
    row=[]
    atm_model=[]
    for altitude in orbit:
        alt=altitude
        res=msise_model(datetime(year,month,day,hour,mins,sec), alt,log,lat,f107,f107,ap,lst=lst)
        row=[]
        row.append(res[0][1])
        row.append(res[0][2])
        row.append(res[0][3])
        row.append(res[0][0])
        row.append(res[0][6])
        atm_model.append(row)
        
    return atm_model #number of particles for [O,N2,O2,He,H]
    
    

#THRUST

def get_thrust(f107):

    #Beam current


    Ib=[]
    Ib_row=[]
    #for rows in atm_solar_avg:
    atm_model=get_model(f107)
    for rows in atm_model:
        Ib_row=[]
        for element in v_ex:
            num=v_ex.index(element)
            x=1/2*Tg*Ag*q*element*10**6
            Ib_row.append(x*float(rows[num])) #Ib=1/2*Tg*Ag*q*vexhaust*ni

        Ib.append(Ib_row)

    Ib_all=[]
    for row in Ib:
        sum=0
        for element in row:
            sum=element+sum

        Ib_all.append(sum)


    #Specific Impulse
    Isp=[]
    for element in mol_mass:
        Isp.append(1/go*math.sqrt(2*q/element*1000)) #Isp=1/g*sqrt(2*q/mi)



    #Epsilon RAM

    eRAM=[]
    eRAM_row=[]
    for velocity in v_orbit:
        eRAM_row=[]
        for element in Isp:
            eRAM_row.append((go*element-velocity)/(go*element)) #eRAM=(Isp*g-vorbit)/g*Isp

        eRAM.append(eRAM_row)
    
    #Thrust
    T=[]
    T_row=[]
    k=0
    for row in Ib:
        T_row=[]
        for element in mol_mass:
            num=mol_mass.index(element)
            T_row.append(eRAM[k][num]*eta_z*eta_i*row[num]*math.sqrt(2*element/q)*math.sqrt(V)) #T=eRAM*etaz*etai*Ib*sqrt(2*mi/q)*sqrt(V)
        k=k+1
        T.append(T_row)

    T_all=[]
    for row in T:
        sum=0
        for element in row:
            sum=element+sum

        T_all.append(sum)
        
    return T_all

#Drag

def get_drag(f107):


    D=[]
    D_row=[]
    atmo_hustota_sum=get_density(f107)
    for density in atmo_hustota_sum:
        D_row=[]
        num=atmo_hustota_sum.index(density)
        for element in Ar:
            
            D_row.append(1/2*Cd*element*v_orbit[num]**2*density) #D=1/2*Cd*A*vorbit^2*ro
        
        D.append(D_row)

    D_plus_T=[]
    k=0
    T=get_thrust(f107)
    for rows in D:
        rows.append(T[k])
        D_plus_T.append(rows)
    
        k=k+1
    return D_plus_T


#Density / for Drag calculation
def get_density(f107):
    atmo_hustota_row=[]
    atmo_hustota=[]
    atm_model=get_model(f107)
    for rows in atm_model:
        atmo_hustota_row=[]
        for element in mol_mass:
            num=mol_mass.index(element)
            atmo_hustota_row.append(float(rows[num])*10**6*element)
        atmo_hustota.append(atmo_hustota_row)


    density=[]
    for row in atmo_hustota:
        sum=0
        for element in row:
            sum=element+sum
        
        density.append(sum)
    
    return density

#Density at a specific altitude / important for orbit decay calculation
def get_specific_density(alt,f107):
    

    #Poradi co potrebuji: O[1], N2[2], O2[3], He[0], H[6]

    res=msise_model(datetime(year,month,day,hour,mins,sec), alt,log,lat,f107,f107,ap,lst=lst)
    atm_model=[]
    atm_model.append(res[0][1])
    atm_model.append(res[0][2])
    atm_model.append(res[0][3])
    atm_model.append(res[0][0])
    atm_model.append(res[0][6])
    
    
    atmo_hustota=0
    spec_density=0
    for  element in atm_model:
        num=atm_model.index(element)
        atmo_hustota=element*10**6*mol_mass[num]
        spec_density=atmo_hustota+spec_density

    
    return spec_density


***
### 4. Select Plot 

  1. __Atmospheric Drag and Thrust__
     - Atmospheric Drag and Thrust for different altitudes
     - Sliders for different values of __Cd__ and  __$\eta$<sub>z</sub>__
     - Vertical slider for different values of __solar flux__
<p>&nbsp;</p> 
  2. __Atomic Oxygen contamination__
      - Number of particles that could interact with ram area surface
      - Sliders for different __altitudes__, __Ram area__ and __time__ spent on orbit
<p>&nbsp;</p>      
  3. __Orbit decay__
      - Orbit decay due to drag froces
      - Sliders for different __initial altitude__, __RAM area__ and __Cd__
      - Vertical slider for different values of __solar flux__
<p>&nbsp;</p> 
  4. __Thrust-to-Drag ratio | Variable altitude__ 
      - Ratio of available thrust to atmospheric drag
      - Sliders for different values of __Grid Radius__, __Grid Voltage__, __$\eta$<sub>i</sub>__, __$\eta$<sub>z</sub>__, __Cd__
      - Vertical slider for different values of __solar flux__
      - Button for showing T/D ratio for __500/1000/1500 V__ Grid Voltage
<p>&nbsp;</p> 
  5. __Thrust-to-Drag ratio | Variable $\eta$<sub>i</sub>__ 
      - Ratio of available thrust to atmospheric drag for given altitude
      - Sliders for different values of __Grid Radius__, __Grid Voltage__, __$\eta$<sub>z</sub>__, __Cd__
      - Vertical slider for different values of __solar flux__
      - Button for showing T/D ratio for __2 - 10 %__ ionization efficiency


     

In [4]:
# 1 = Drag/Thrust
# 2 = Atomic Oxygen
# 3 - Orbit Decay
# 4 - T/D ratio | Variable Altitude
# 5 - T/D ratio | Variable Ionization efficiency

plot=1

### Plot functions

In [52]:
axcolor="ivory" #Color of sliders and buttons
#================================================

def get_drag_xdata(f107):
        x=[]
        drag_data=get_drag(f107)
        for index in range (0,len(drag_data[0])):    
            x.append([row[index] for row in drag_data]) #X axes
        return x
    
#================================================

#====== Output variables for CSV ========

CdOutput=0
etazOutput=0
solarOutput=0
    
#===========================================================================================================
#=============== DRAG PLOT ==================
#=========================================================================================================== 
if plot==1:
    
    
    
    fig, ax = plt.subplots()
    fig.text(0.95, 0.5, 'Solar Activity', rotation=-90)
    plt.subplots_adjust(left=0.15, bottom=0.3) #Configure plot size and design
    plt.xscale("log")
    plt.title('Atmospheric drag and achievable thrust')
    plt.xlabel('Drag [N]')
    plt.ylabel('Altitude [km]')

    if Ar_classic == 1:

        labels=["U3 Drag","U6 Drag","U8 Drag","U27 Drag","Thrust"] #Labels for a legend
    else:
        labels=["Drag","Thrust"]
    yD=orbit #Y axes
    xD=get_drag_xdata(solar_avg) #X axes

    l=['l%d' % i for i in range(0, len(xD), 1)] #Plotting of different plots
    for i in range (0, len(xD), 1):
        l[i],=plt.plot(xD[i], yD, lw=1, label=labels[i])

    ax.margins(x=0) #Margins on a X axes
    plt.legend(loc="upper right") #Legend plotting

    #======== Drag Sliders==================
    axCdD = plt.axes([0.25, 0.06, 0.65, 0.03], facecolor=axcolor) #Sliders design and position
    axEtazD = plt.axes([0.25, 0.02, 0.65, 0.03], facecolor=axcolor)
    axSolD = plt.axes([0.92, 0.25, 0.03, 0.60], facecolor=axcolor)
    axEtaiD = plt.axes([0.25, 0.1, 0.65, 0.03], facecolor=axcolor)
    axVoltD = plt.axes([0.25, 0.14, 0.65, 0.03], facecolor=axcolor)

    delta_fD = 0.1 #Configure sliders step
    delta_etazD=0.1
    delta_solD=15
    delta_etaiD=0.01
    delta_voltD=10
    Cd0D=2.2 #Slider init value
    Etaz0D=0.9
    Sol0D=solar_avg
    Etai0D=0.1
    Volt0D=V
    sCdD = Slider(axCdD, 'Cd [-]', 0.1, 5.0, valinit=Cd0D,valstep=delta_fD) #Slider values
    sEtazD = Slider(axEtazD, 'eta z [-]', 0.1, 1, valinit=Etaz0D,valstep=delta_etazD)
    sSolD = Slider(axSolD,"", solar_min, solar_max, valinit=Sol0D,valstep=delta_solD, orientation="vertical")
    sEtaiD = Slider(axEtaiD, 'eta i [-]', 0.01, 0.3, valinit=Etai0D,valstep=delta_etaiD)
    sVoltD = Slider(axVoltD, 'Grid Voltage [V]', 100, 2000, valinit=Volt0D,valstep=delta_voltD)
    
    #============ Global variables ===============
    
    thrust_flag=0
    drag_flag=0
    #============================================
    #========== CSV Variables ==========
    
    xDoutput=xD
    yDoutput=yD
    CdOutput-Cd0D
    solarOutput=Sol0D
    etazOutput=Etaz0D
    
    #========================================
    
    def update(val): #Update plot after slider change

        Cdd = sCdD.val #Values of Drag sliders
        etaz=sEtazD.val
        sold=sSolD.val
        etaid=sEtaiD.val
        voltd=sVoltD.val
        
        global xDoutput
        global Cdoutput
        global etazOutput
        global solarOutput
        CdOutput=Cdd
        etazOutput=etaz
        solarOutput=sold
        xDoutput=[]     
           
        #======= Drag Slider logic============
        xD=get_drag_xdata(sold)

        for i in range (0, len(xD)-1, 1): #Showing both
            xDoutput.append([Cdd*element/Cd0D for element in xD[i]])
            l[i].set_xdata([Cdd*element/Cd0D for element in xD[i]]) #Updating X data with new values of Cd

        if thrust_flag==1: # Showing only Thrust
            for i in range (0, len(xD)-1, 1):
                #xDoutput.append([Cdd*element/Cd0D for element in xD[i]])
                l[i].set_xdata([0*element for element in xD[i]]) #Empty drag

        l[len(xD)-1].set_xdata([(etaz/eta_z)*(etaid/eta_i)*(math.sqrt(voltd)/math.sqrt(V))*element for element in xD[len(xD)-1]]) #Updating Thrust data with new value EtaZ
        xDoutput.append([(etaz/eta_z)*(etaid/eta_i)*(math.sqrt(voltd)/math.sqrt(V))*element for element in xD[len(xD)-1]])

        if drag_flag==1: # Showing only Drag
            #xDoutput.append([etaz*element/eta_z for element in xD[len(xD)-1]])
            l[len(xD)-1].set_xdata([0*element for element in xD[len(xD)-1]]) #Empty Thrust data
                
         #===============================
        fig.canvas.draw_idle()

    sCdD.on_changed(update) #Sliders for Drag
    sEtazD.on_changed(update)
    sSolD.on_changed(update)
    sEtaiD.on_changed(update)
    sVoltD.on_changed(update)
    
    #====Drag show only thrust Button ======
    thrustax = plt.axes([0.25, 0.95, 0.22, 0.04]) #button configuration
    buttonThrust = Button(thrustax, 'Toggle Drag On/Off', color=axcolor, hovercolor='0.975')

    def show_thrust(event): #show original plot
        global thrust_flag
        if thrust_flag ==0:
            thrust_flag = 1
        else:
            thrust_flag = 0
        
    buttonThrust.on_clicked(show_thrust)
    buttonThrust.on_clicked(update)
    plt.show()
    
    #====Drag show only drag Button ======
    dragax = plt.axes([0.5, 0.95, 0.22, 0.04]) #button configuration
    buttonDrag = Button(dragax, 'Toggle Thrust On/Off', color=axcolor, hovercolor='0.975')

    def show_drag(event): #show original plot
        global drag_flag
        if drag_flag ==0:
            drag_flag = 1
        else:
            drag_flag = 0
        
    buttonDrag.on_clicked(show_drag)
    buttonDrag.on_clicked(update)
    plt.show()
    
#=========================================================================================================== 
#================== ATOMIC OXYGEN PLOT ========================
#=========================================================================================================== 
elif plot==2:
    
    #Y Data - Amount of O
    #Obtaining Oxygen
    #=====
    o_all=[]
    o_array=[]
    solar=[solar_min,solar_avg,solar_max]
    for s in solar: # Getting atomic oxygen values for 3 different solar activities
        o_all=[]
        for a in orbit:
            res=msise_model(datetime(year,month,day,hour,mins,sec), a,log,lat,s,s,ap,lst=lst)
            o_all.append(res[0][1]*10**-6)  #only atomic oxygen [particles/m3]
        o_array.append(o_all)
    #=====

    #Init values
    Time0=1 #Days
    Alt0=initAlt #Innitial altitude
    Ar0Body=Ar[0]-Ainlet #Ram area
    Ar0Inlet=Ainlet
    
    indexAlt=orbit.index(Alt0) # index for init value of oxygen
    indexVelocity=Alt0/intval+1 #index for init value of orbital velocity

    oxy=[ox[indexAlt]*(Ar0Body+Ar0Inlet)*v_orbit[int(indexVelocity)]*secs for ox in o_array] #Particles for different solar activites per 1day

    #=================== Plotting ================================
    labels=["Sol MIN","Sol AVG","Sol MAX"] #Labels for legend plotting
    fig, ax = plt.subplots()
    plt.subplots_adjust(left=0.15, bottom=0.35)
    plt.yscale("log")
    plt.title("Atomic oxygen collisions over time")
    plt.ylabel("Particles [-]")
    width=0.25
    ax.bar(labels,oxy, width, label="")
    #====

    #AO Sliders
    axTime = plt.axes([0.25, 0.1, 0.65, 0.03], facecolor=axcolor) #Sliders design and position
    axAlt = plt.axes([0.25, 0.05, 0.65, 0.03], facecolor=axcolor)
    axAreaBody = plt.axes([0.25, 0.15, 0.65, 0.03], facecolor=axcolor)
    axAreaInlet = plt.axes([0.25, 0.20, 0.65, 0.03], facecolor=axcolor)

    delta_time = 1 #Configure sliders step
    delta_alt=5
    delta_areaBody=0.01
    delta_areaInlet=0.01

    sTime = Slider(axTime, 'Time [Days]', 1, 2*365, valinit=Time0,valstep=delta_time) #Slider values
    sAlt = Slider(axAlt, 'Altitude [km]', minalt, maxalt, valinit=Alt0,valstep=delta_alt)
    sAreaBody = Slider(axAreaBody,"RAM Area Body [m2]", 0.01, 0.5, valinit=Ar0Body,valstep=delta_areaBody)
    sAreaInlet = Slider(axAreaInlet,"RAM Area Inlet [m2]", 0.01, 0.5, valinit=Ar0Inlet,valstep=delta_areaBody)

    #==== for CSV saving ===
    aglobal=Alt0
    tglobal=Time0
    areabodyglobal=Ar0Body
    areainletglobal=Ar0Inlet
    oxyglobal=oxy
    #=======================
    
    inlet_flag=0
    
    def update(val): #Update plot after slider change

        t = sTime.val #Values of AO sliders
        a = sAlt.val
        areaBody=sAreaBody.val
        areaInlet=sAreaInlet.val

        #======= AO Slider logic============
        indAlt=orbit.index(a)
        indVel=a/intval+1

        if inlet_flag==0:
            oxynew=[ox[indAlt]*(areaBody+areaInlet)*v_orbit[int(indVel)]*secs*t for ox in o_array] #Particles per X days for cubesatbody + inlet
        elif inlet_flag==1:
            oxynew=[ox[indAlt]*areaInlet*v_orbit[int(indVel)]*secs*t for ox in o_array] #Particles per X days for only inlet area
        
        
        global aglobal
        global tglobal
        global areabodyglobal
        global areainletglobal
        global oxyglobal
        
        aglobal=a
        tglobal=t
        areabodyglobal=areaBody
        areainletglobal=areaInlet
        oxyglobal=oxynew
    
        #========== Updated Plotting ===================
        ax.clear()
        ax.set_title("Atomic oxygen collisions over time")
        if inlet_flag==1:
            ax.set_title("Atomic oxygen collisions over time | Inlet")
        ax.set_yscale("log")
        ax.bar(labels,oxynew, width, label="Custom value", color="RED")
        ax.bar(labels,oxy, width, label="Original value")
        ax.set_ylabel('Particles [-]')
        ax.legend()
        #===================
        fig.canvas.draw_idle()
        
    sTime.on_changed(update) #Sliders for AO
    sAlt.on_changed(update)
    sAreaBody.on_changed(update)
    sAreaInlet.on_changed(update)
    
    #========Only inlet Button ======
    inletax = plt.axes([0.25, 0.95, 0.25, 0.04]) #button configuration
    buttonInlet = Button(inletax, 'Show only Inlet', color=axcolor, hovercolor='0.975')

    def show_inlet(event): #delete original plot
        global inlet_flag
        if inlet_flag ==0:
            inlet_flag = 1
        else:
            inlet_flag = 0
    buttonInlet.on_clicked(show_inlet)
    buttonInlet.on_clicked(update)
    plt.show()



#=========================================================================================================== 
#=============================================== ORBIT DECAY PLOT ==================
#=========================================================================================================== 
elif plot==3:
    
    def get_decay_data(Cd,Ar,Thrust,alt0,sol):

        ndays=100000

        dT=secs #Time increment 1day in secs

        a=(Rz+alt0)*1000 # calculation of init altitude in [m]
        P=2*np.pi*np.sqrt(a**3/(Mz*G)) #calculation of init orbit period [s]
        

        newAlt=a/1000-Rz #altitude in [km]

        alti=[newAlt] #Y axes for graph
        days=[0] #X axes for graph
        Thrust = Thrust * 10**-3 #mN
        for rep in range (0,ndays):
            D=1/2*Cd*G*Mz*Ar/a*get_specific_density((newAlt),sol)#Calculating the drag for given altitude and solar flux

            D=D-Thrust
            dP=6*np.pi*(a**2)*D/G/Mz/m*dT #Calculation the orbit period change for given drag
            P=P-dP #new orbit period
            a=(P**2/(4*np.pi**2)*Mz*G)**(1/3) #new altitude+earth radius [m]
            newAlt=a/1000-Rz #new altitude above the earth surface [km]

            if newAlt>alt0+100 or newAlt<0: #correction for non valid outputs adn end of the cycle when orbit is 0
                newAlt=0
                break

            alti.append(newAlt) #Y
            days.append(rep) #X

        return alti,days
    
    def get_decay_data_minutes(Cd,Ar,Thrust,alt0,sol):

        ndays=100000

        dT=60 #Time increment 1min in secs

        a=(Rz+alt0)*1000 # calculation of init altitude in [m]
        P=2*np.pi*np.sqrt(a**3/(Mz*G)) #calculation of init orbit period [s]
        

        newAlt=a/1000-Rz #altitude in [km]

        alti=[newAlt] #Y axes for graph
        minutes=[0] #X axes for graph
        Thrust = Thrust * 10**-3 #mN
        for rep in range (0,ndays):
            D=1/2*Cd*G*Mz*Ar/a*get_specific_density((newAlt),sol)#Calculating the drag for given altitude and solar flux

            D=D-Thrust
            dP=6*np.pi*(a**2)*D/G/Mz/m*dT #Calculation the orbit period change for given drag
            P=P-dP #new orbit period
            a=(P**2/(4*np.pi**2)*Mz*G)**(1/3) #new altitude+earth radius [m]
            newAlt=a/1000-Rz #new altitude above the earth surface [km]

            if newAlt>alt0+100 or newAlt<0: #correction for non valid outputs adn end of the cycle when orbit is 0
                newAlt=0
                break

            alti.append(newAlt*1000) #Y
            minutes.append(rep) #X

        return alti,minutes


    #======== Plotting =============

    fig, ax = plt.subplots()
    fig.text(0.95, 0.5, 'Solar Activity', rotation=-90)
    plt.subplots_adjust(left=0.15, bottom=0.35) #Configure plot size and design
    plt.title('Orbit decay')
    plt.xlabel('Time [days]')
    plt.ylabel('Altitude [km]')



    yorig=get_decay_data(Cd,Ar[0],0,initAlt,solar_avg)[0] #Y axes
    xorig=get_decay_data(Cd,Ar[0],0,initAlt,solar_avg)[1] #X axes
    Cdorig=Cd
    
    delete_flag=0
    showmin_flag=0

    p,=plt.plot(xorig, yorig, lw=1)
    ax.margins(x=0) #Margins on a X axes


    #========== Sliders ================
    axCdO = plt.axes([0.25, 0.1, 0.65, 0.03], facecolor=axcolor) #Sliders design and position
    axThO = plt.axes([0.25, 0.05, 0.65, 0.03], facecolor=axcolor)
    axSolO = plt.axes([0.92, 0.30, 0.03, 0.60], facecolor=axcolor)
    axAltO = plt.axes([0.25, 0.15, 0.65, 0.03], facecolor=axcolor)
    axArO = plt.axes([0.25, 0.20, 0.65, 0.03], facecolor=axcolor)


    delta_cdO = 0.1 #Configure sliders step
    delta_thO=0.00001
    delta_solO=15
    delta_altO=5
    delta_arO=0.01
    Cd0O=Cd #Slider init value
    Th0O=0
    Sol0O=solar_avg
    Alt0O=initAlt
    Ar0O=Ar[0]
    sCdO = Slider(axCdO, 'Cd [-]', 0.1, 5.0, valinit=Cd0O,valstep=delta_cdO) #Slider values
    sThO = Slider(axThO, 'Thrust [mN]', 0.001, 5, valinit=Th0O,valstep=delta_thO)
    sSolO = Slider(axSolO,"", solar_min, solar_max, valinit=Sol0O,valstep=delta_solO, orientation="vertical")
    sAltO = Slider(axAltO, 'Altitude [km]', 80, 600, valinit=Alt0O,valstep=delta_altO)
    sArO = Slider(axArO, 'RAM area [m^2]', 0.01, 0.5, valinit=Ar0O,valstep=delta_arO)
    #===========================================
    
    #==== Global results for CSV ====
    xglobal=xorig
    yglobal=yorig
    thrustGlobal=Th0O
    ramGlobal=Ar0O
    CdOutput=Cd0O
    solarOutput=Sol0O
    #========================

    def update(val):

        Cdo = sCdO.val #Values of Decay sliders
        Th=sThO.val
        solo=sSolO.val
        alt=sAltO.val
        aro=sArO.val
        #======= Decay Orbit Slider logic ===============
        yO=get_decay_data(Cdo,aro,Th,alt,solo)[0] #new values of x/y
        xO=get_decay_data(Cdo,aro,Th,alt,solo)[1]

        yorigO=get_decay_data(Cdorig,Ar[0],0,alt,solar_avg)[0] #original values, but new value of init altitude for graph readability
        xorigO=get_decay_data(Cdorig,Ar[0],0,alt,solar_avg)[1]

        global xglobal
        global yglobal
        global thrustGlobal
        global ramGlobal
        global CdOuput
        global solarOutput
        
        xglobal=xO
        yglobal=yO
        
        thrustGlobal=Th
        ramGlobal=aro
        CdOutput=Cdo
        solarOutput=solo
        
        
        ax.clear() #redrawing plots
        if delete_flag==0:
            ax.plot(xorigO, yorigO, lw=1,label="Original value",color="RED")
        ax.plot(xO, yO, lw=1,label="Custom value",color="BLUE")
        ax.set_title("Orbit decay")
        ax.set_xlabel('Time [days]')
        ax.set_ylabel('Altitude [km]')
        ax.legend()
        
        if showmin_flag==1:
            
                
            yOMeter=get_decay_data_minutes(Cdo,aro,Th,alt,solo)[0] #new values of x/y
            xOMin=get_decay_data_minutes(Cdo,aro,Th,alt,solo)[1]

            yorigOMeter=get_decay_data_minutes(Cdorig,Ar[0],0,alt,solar_avg)[0] #original values, but new value of init altitude for graph readability
            xorigOMin=get_decay_data_minutes(Cdorig,Ar[0],0,alt,solar_avg)[1]
            
            xglobal=xOMin
            yglobal=yOMeter
                
            ax.plot(xorigOMin, yorigOMeter, lw=1,label="Original value",color="RED")
            ax.plot(xOMin, yOMeter, lw=1,label="Custom value",color="BLUE")
            ax.set_title("Orbit decay")
            ax.set_xlabel('Time [min]')
            ax.set_ylabel('Altitude [m]')
            ax.legend()

        #======================================
        fig.canvas.draw_idle()
        
        


    sCdO.on_changed(update) #Sliders for Decay
    sThO.on_changed(update)
    sSolO.on_changed(update)
    sAltO.on_changed(update)
    sArO.on_changed(update)
    
    #====Decay delete original Button ======
    delax = plt.axes([0.25, 0.95, 0.25, 0.04]) #button configuration
    buttonD = Button(delax, 'Toggle Original On/Off', color=axcolor, hovercolor='0.975')

    def delete_original(event): #delete original plot
        global delete_flag
        if delete_flag ==0:
            delete_flag = 1
        else:
            delete_flag = 0
    buttonD.on_clicked(delete_original)
    buttonD.on_clicked(update)
    plt.show()
    
    #====Decay minutes Button ======
    minax = plt.axes([0.55, 0.95, 0.25, 0.04]) #button configuration
    buttonMin = Button(minax, 'Toggle Time Min/Day', color=axcolor, hovercolor='0.975')

    def show_min(event): #delete original plot
        global showmin_flag
        if showmin_flag ==0:
            showmin_flag = 1
        else:
            showmin_flag = 0
    buttonMin.on_clicked(show_min)
    buttonMin.on_clicked(update)
    plt.show()

#=========================================================================================================== 
#================ T/D RATIO PLOT =======================
#=========================================================================================================== 
elif plot==4:

    
    yTD=orbit#Y axes
    xTD=get_drag_xdata(solar_avg) #X axes, values of drag and thrust
    
    #===============Calculation of T/D ratio======================
    
    T=xTD[-1] #Thrust
    D=xTD[0] #Drag
    TD=[]
    for i in range (0,len(T)):
        TD.append(T[i]/D[i]) #T/D ratio
        
    TD500=[]
    TD1000=[]
    TD1500=[]
    for element in TD: #Values of TD ratio for voltage levels of 500V/1000V/1500V
            
        TD500.append((math.sqrt(500)/math.sqrt(V))*element)
        TD1000.append((math.sqrt(1000)/math.sqrt(V))*element)
        TD1500.append((math.sqrt(1500)/math.sqrt(V))*element)
      
    #=============================================================
    
    agrlimit=np.sqrt(Ainlet/np.pi) #Max acc grid radius for given inlet radius
    #==========================================
    
    fig, ax = plt.subplots()
    fig.text(0.95, 0.5, 'Solar Activity', rotation=-90)
    plt.subplots_adjust(left=0.15, bottom=0.35) #Configure plot size and design
    plt.title('T/D plot')
    plt.xlabel('T/D ratio [-]')
    plt.ylabel('Altitude [km]')
    ax.plot(TD, yTD, lw=1,label="T/D ratio",color="BLUE")
    ax.legend()
    
    ax.margins(x=0) #Margins on a X axes
    plt.legend(loc="upper right") #Legend plotting

    
    
    #TD Sliders
    axCdTD = plt.axes([0.25, 0.03, 0.65, 0.03], facecolor=axcolor) #Sliders design and position
    axEtazTD = plt.axes([0.25, 0.08, 0.65, 0.03], facecolor=axcolor)
    axEtaiTD = plt.axes([0.25, 0.12, 0.65, 0.03], facecolor=axcolor)
    axVoltTD = plt.axes([0.25, 0.17, 0.65, 0.03], facecolor=axcolor)
    axAgrTD = plt.axes([0.25, 0.22, 0.65, 0.03], facecolor=axcolor)
    axSolTD = plt.axes([0.92, 0.35, 0.03, 0.60], facecolor=axcolor)

    
    delta_cdTD = 0.1 #Configure sliders step
    delta_etazTD=0.1
    delta_solTD=15
    delta_etaiTD=0.01
    delta_volt=10
    delta_agrTD=0.001
    Cd0TD=2.2 #Slider init value
    Etaz0TD=0.9
    Etai0TD=0.1
    Volt0=V
    Agr0TD=math.sqrt(Ag/(np.pi))
    Sol0TD=solar_avg
    sCdTD = Slider(axCdTD, 'Cd', 0.1, 5.0, valinit=Cd0TD,valstep=delta_cdTD) #Slider values
    sEtazTD = Slider(axEtazTD, 'eta z', 0.1, 1, valinit=Etaz0TD,valstep=delta_etazTD)
    sEtaiTD = Slider(axEtaiTD, 'eta i', 0.01, 0.3, valinit=Etai0TD,valstep=delta_etaiTD)
    sVoltTD = Slider(axVoltTD, 'Grid Voltage', 100, 5000, valinit=Volt0,valstep=delta_volt)
    sAgrTD = Slider(axAgrTD, 'Grid Radius', 0.001, agrlimit, valinit=Agr0TD,valstep=delta_agrTD)
    sSolTD = Slider(axSolTD,"", solar_min, solar_max, valinit=Sol0TD,valstep=delta_solTD, orientation="vertical")
    
    delete_flag=1
    showV_flag=0

    #output values for csv saving
    Doutput=D
    TDoutput=TD
    TDvoloutput=[TD500, TD1000, TD1500]
    Altitudeoutput=yTD
    CdOutput=Cd0TD
    solarOutput=Sol0TD
    etazOutput=Etaz0TD
    gridRadiusOutput=Agr0TD 
    gridVoltageOutput=Volt0
    etaiOutput=Etai0TD
    

    def update(val): #Update plot after slider change

        Cdtd = sCdTD.val #Values of Drag sliders
        etaztd=sEtazTD.val
        soltd=sSolTD.val
        etaitd=sEtaiTD.val
        volt=sVoltTD.val
        ag=np.pi*sAgrTD.val**2
        
        TDnew=[]
        xTDnew=get_drag_xdata(soltd)
        

        Tnew=xTDnew[-1]
        Dnew=xTDnew[0]

        
        for i in range (0,len(Tnew)): #Calculation of new Thrust / Drag value with a slider value of etaz, etai, V, Cd
            TDnew.append((etaztd/eta_z)*(etaitd/eta_i)*(math.sqrt(volt)/math.sqrt(V))*(ag/Ag)*Tnew[i]/((Cdtd/Cd)*Dnew[i]))
            
         
        TDnew500=[]
        TDnew1000=[]
        TDnew1500=[]

        for element in TDnew: #Values of TD ratio for voltage levels of 500V/1000V/1500V
            
            TDnew500.append((math.sqrt(500)/math.sqrt(volt))*element)
            TDnew1000.append((math.sqrt(1000)/math.sqrt(volt))*element)
            TDnew1500.append((math.sqrt(1500)/math.sqrt(volt))*element)
            
        global delete_flag
        global Doutput
        global TDoutput
        global TDvoloutput
        global CdOutput
        global solarOutput
        global etazOutput
        global gridRadiusOutput
        global gridVoltageOutput
        global etaiOutput
        
        Doutput=Dnew
        TDoutput=TDnew
        TDvoloutput=[TDnew500, TDnew1000, TDnew1500]
        CdOutput=Cdtd
        solarOutput=soltd
        etazOutput=etaztd
        gridRadiusOutput=ag
        gridVoltageOutput=volt
        etaiOutput=etaitd#Output for CSV

        ax.clear()
        if delete_flag==1:
            ax.plot(TD, yTD, lw=1,label="T/D Original ratio",color="RED")
        
        if showV_flag==1:
            ax.plot(TDnew500, yTD, lw=1,label="T/D Custom ratio 500 V",color="BLACK")
            ax.plot(TDnew1000, yTD, lw=1,label="T/D Custom ratio 1000 V",color="ORANGE")
            ax.plot(TDnew1500, yTD, lw=1,label="T/D Custom ratio 1500 V",color="GREEN")
            
        ax.plot(TDnew, yTD, lw=1,label="T/D Custom ratio",color="BLUE")
        ax.set_title("T/D ratio plot")
        ax.set_xlabel('T/D ratio [-]')
        ax.set_ylabel('Altitude [km]')
        ax.legend()

        
        fig.canvas.draw_idle()

    sCdTD.on_changed(update) #Sliders for Drag
    sEtazTD.on_changed(update)
    sSolTD.on_changed(update)
    sEtaiTD.on_changed(update)
    sVoltTD.on_changed(update)
    sAgrTD.on_changed(update)
    
    
    #====TD delete original Button ======
    delax = plt.axes([0.25, 0.95, 0.25, 0.04]) #button configuration
    buttonD = Button(delax, 'Toggle Original On/Off', color=axcolor, hovercolor='0.975')

    def delete_original(event): #delete original plot
        global delete_flag
        if delete_flag ==0:
            delete_flag = 1
        else:
            delete_flag = 0

    buttonD.on_clicked(delete_original)
    buttonD.on_clicked(update)
    plt.show()
    
    #====TD show set voltage Button ======
    setVolax = plt.axes([0.55, 0.95, 0.35, 0.04]) #button configuration
    buttonVol = Button(setVolax, 'Toggle 500/1000/1500 V On/Off', color=axcolor, hovercolor='0.975')

    def show_setVoltage(event): # Show values for 500/1000/1500 V
        global showV_flag
        if showV_flag ==0:
            showV_flag = 1
        else:
            showV_flag = 0

    buttonVol.on_clicked(show_setVoltage)
    buttonVol.on_clicked(update)
    plt.show()

#=========================================================================================================== 
#===============TD Plot 2 - specific altitude, variable eta i ===============================
#=========================================================================================================== 
elif plot==5:

    
    
    yTD=np.arange(0.1,1,0.1).tolist() #Y axes
    xTD=get_drag_xdata(solar_avg) #X axes
    
    initOrbit=250
    def get_altIndex(chosenOrbit):
        for element in orbit:  
            if element>=chosenOrbit:
                ind=orbit.index(element)
                break
        return ind
    

    #===============Calculation of T/D ratio======================
    

    Tspec=xTD[-1][get_altIndex(initOrbit)] #Thrust at specific altitude
    Dspec=xTD[0][get_altIndex(initOrbit)]  #Drag at specific altitude
    
    TDspec=[]
    for element in yTD:
        TspecNew=Tspec*element/eta_z
        TDspec.append(TspecNew/Dspec) #T/D ratio for specific altitude
        
    #=============================================================

    agrlimit=np.sqrt((Ar[0]-0.03)/np.pi)
    #==========================================

    fig, ax = plt.subplots()
    fig.text(0.95, 0.5, 'Solar Activity', rotation=-90)
    plt.subplots_adjust(left=0.15, bottom=0.35) #Configure plot size and design
    plt.title('T/D plot')
    plt.xlabel('T/D ratio [-]')
    plt.ylabel('Capture eff [-]')
    ax.plot(TDspec, yTD, lw=1,label="T/D ratio",color="BLUE")
    ax.legend()

    ax.margins(x=0) #Margins on a X axes
    plt.legend(loc="upper right") #Legend plotting



    #TD Sliders
    axCdTD = plt.axes([0.25, 0.08, 0.65, 0.03], facecolor=axcolor) #Sliders design and position
    axAltTD = plt.axes([0.25, 0.03, 0.65, 0.03], facecolor=axcolor)
    axEtaiTD = plt.axes([0.25, 0.13, 0.65, 0.03], facecolor=axcolor)
    axVoltTD = plt.axes([0.25, 0.18, 0.65, 0.03], facecolor=axcolor)
    axAgrTD = plt.axes([0.25, 0.23, 0.65, 0.03], facecolor=axcolor)
    axSolTD = plt.axes([0.92, 0.35, 0.03, 0.60], facecolor=axcolor)


    delta_fTD = 0.1 #Configure sliders step
    delta_altTD=5
    delta_solTD=15
    delta_etaiTD=0.01
    delta_voltTD=10
    delta_agrTD=0.001
    Cd0TD=2.2 #Slider init value
    Alt0TD=initOrbit
    Etai0TD=0.1
    Volt0=V
    Agr0TD=math.sqrt(Ag/(np.pi))
    Sol0TD=solar_avg
    sCdTD = Slider(axCdTD, 'Cd [-]', 0.1, 5.0, valinit=Cd0TD,valstep=delta_fTD) #Slider values
    sAltTD = Slider(axAltTD, 'Altitude [km]', minalt, maxalt, valinit=Alt0TD,valstep=delta_altTD)
    sEtaiTD = Slider(axEtaiTD, 'eta i', 0.01, 0.3, valinit=Etai0TD,valstep=delta_etaiTD)
    sVoltTD = Slider(axVoltTD, 'Grid Voltage [V]', 100, 2000, valinit=Volt0,valstep=delta_voltTD)
    sAgrTD = Slider(axAgrTD, 'Grid Radius [m]', 0.001, agrlimit, valinit=Agr0TD,valstep=delta_agrTD)
    sSolTD = Slider(axSolTD,"", solar_min, solar_max, valinit=Sol0TD,valstep=delta_solTD, orientation="vertical")

    delete_flag=1
    showlegend_flag=1
    showAll_flag=0
    updated=0

    #output values for csv saving
    TDArroutput=[]
    TDspecoutput=TDspec
    Dspecoutput=Dspec
    Etazoutput=yTD
    CdOutput=Cd0TD
    solarOutput=Sol0TD
    gridRadiusOutput=Agr0TD 
    gridVoltageOutput=Volt0
    etaiOutput=Etai0TD
    altiOutput=Alt0TD
    #-------------

    def update(val): #Update plot after slider change

        Cdtd2 = sCdTD.val #Values of Drag sliders
        alttd2=sAltTD.val
        soltd2=sSolTD.val
        etaitd2=sEtaiTD.val
        volt2=sVoltTD.val
        ag2=np.pi*sAgrTD.val**2

        global delete_flag
        global showleg_flag
        global showAll_flag
        global updated
        updated = 1

        global DArroutput
        global TDArroutput
        global TDspecoutput
        global CdOutput
        global solarOutput
        global gridRadiusOutput
        global gridVoltageOutput
        global etaiOutput
        global altiOutput

        xTDnew=get_drag_xdata(soltd2)

        Tspecnew=xTDnew[-1][get_altIndex(alttd2)] #Thrust values for specific altitude
        Dspecnew=xTDnew[0][get_altIndex(alttd2)] #Drag values for specific altitude
        
        DArroutput=[]
        TDspecnew=[]
        TDspecEtai2=[]
        TDspecEtai3=[]
        TDspecEtai4=[]
        TDspecEtai5=[]
        TDspecEtai6=[]
        TDspecEtai7=[]
        TDspecEtai8=[]
        TDspecEtai9=[]
        TDspecEtai10=[]

        for element in yTD:
            tspec=Tspecnew*element/eta_z
            TDspecnew.append((etaitd2/eta_i)*(math.sqrt(volt2)/math.sqrt(V))*(ag2/Ag)*tspec/((Cdtd2/Cd)*Dspecnew))

        for element in TDspecnew:
            TDspecEtai2.append((0.02/etaitd2)*element)
            TDspecEtai3.append((0.03/etaitd2)*element)
            TDspecEtai4.append((0.04/etaitd2)*element)
            TDspecEtai5.append((0.05/etaitd2)*element)
            TDspecEtai6.append((0.06/etaitd2)*element)
            TDspecEtai7.append((0.07/etaitd2)*element)
            TDspecEtai8.append((0.08/etaitd2)*element)
            TDspecEtai9.append((0.09/etaitd2)*element)
            TDspecEtai10.append((0.10/etaitd2)*element)


        TDArroutput=[TDspecEtai2,TDspecEtai3,TDspecEtai4,TDspecEtai5,TDspecEtai6,TDspecEtai7,TDspecEtai8,TDspecEtai9,TDspecEtai10] #Data for csv output
        TDspecoutput=TDspecnew
        Dspecoutput=Dspecnew
        
        CdOutput=Cdtd2
        solarOutput=soltd2
        gridRadiusOutput=ag2
        gridVoltageOutput=volt2
        etaiOutput=etaitd2
        altiOutput=alttd2

        ax.clear()
        ax.plot(TDspecnew, yTD, lw=1,label="T/D Custom ratio",color="BLUE")

        if delete_flag==1:
            ax.plot(TDspec, yTD, lw=1,label="T/D Original ratio",color="RED")

        if showAll_flag==1:
            ax.plot(TDspecEtai2, yTD, lw=1,label="T/D Custom ratio etai 2%")
            ax.plot(TDspecEtai3, yTD, lw=1,label="T/D Custom ratio etai 3%")
            ax.plot(TDspecEtai4, yTD, lw=1,label="T/D Custom ratio etai 4%")
            ax.plot(TDspecEtai5, yTD, lw=1,label="T/D Custom ratio etai 5%")
            ax.plot(TDspecEtai6, yTD, lw=1,label="T/D Custom ratio etai 6%")
            ax.plot(TDspecEtai7, yTD, lw=1,label="T/D Custom ratio etai 7%")
            ax.plot(TDspecEtai8, yTD, lw=1,label="T/D Custom ratio etai 8%")
            ax.plot(TDspecEtai9, yTD, lw=1,label="T/D Custom ratio etai 9%")
            ax.plot(TDspecEtai10, yTD, lw=1,label="T/D Custom ratio etai 10%")
        ax.set_title("T/D ratio plot")
        ax.set_xlabel('T/D ratio [-]')
        ax.set_ylabel('Capture eff [-]')
        if showlegend_flag==1:
            ax.legend()


        fig.canvas.draw_idle()

    sCdTD.on_changed(update) #Sliders for Drag
    sAltTD.on_changed(update)
    sSolTD.on_changed(update)
    sEtaiTD.on_changed(update)
    sVoltTD.on_changed(update)
    sAgrTD.on_changed(update)


    #====Decay delete original Button ======
    delax = plt.axes([0.22, 0.95, 0.2, 0.04]) #button configuration
    buttonD = Button(delax, 'Original On/Off', color=axcolor, hovercolor='0.975')

    def delete_original(event): #delete original plot
        global delete_flag
        if delete_flag ==0:
            delete_flag = 1
        else:
            delete_flag = 0

    buttonD.on_clicked(delete_original)
    buttonD.on_clicked(update)
    plt.show()

    #====Show legend Button ======
    legendax = plt.axes([0.45, 0.95, 0.2, 0.04]) #button configuration
    buttonL = Button(legendax, 'Legend On/Off', color=axcolor, hovercolor='0.975')

    def show_legend(event): #show legend event
        global showlegend_flag
        if showlegend_flag ==0:
            showlegend_flag = 1
        else:
            showlegend_flag = 0

    buttonL.on_clicked(show_legend)
    buttonL.on_clicked(update)
    plt.show()

    #====Show All efficiencies Button ======
    showAllax = plt.axes([0.68, 0.95, 0.2, 0.04]) #button configuration
    buttonShowAll = Button(showAllax, '1/10 % On/Off', color=axcolor, hovercolor='0.975')

    def show_All(event): #show legend event
        global showAll_flag
        if showAll_flag ==0:
            showAll_flag = 1
        else:
            showAll_flag = 0

    buttonShowAll.on_clicked(show_All)
    buttonShowAll.on_clicked(update)
    plt.show()
    
#===========================================================================================================
#=========================================================================================================== 
    
    
    

    
#====Reset Button ======
resetax = plt.axes([0.8, 0.9, 0.1, 0.04]) #Reset button configuration
buttonReset = Button(resetax, 'Reset', color=axcolor, hovercolor='0.975')

def reset(event): #Reset event
    if plot==1:
        sCdD.reset() #Drag sliders reseting
        sEtazD.reset()
        sSolD.reset()
        sEtaiD.reset()
        sVoltD.reset()
    elif plot==2:
        sTime.reset() #AO sliders reseting
        sAlt.reset()
        sAreaBody.reset()
        sAreaInlet.reset()
    elif plot==3:
        sCdO.reset() #Decay sliders reseting
        sThO.reset()
        sSolO.reset()
        sAltO.reset()
        sArO.reset()
    elif plot==4:
        sCdTD.reset() #Sliders for Thrust/Drag ratio
        sEtazTD.reset()
        sSolTD.reset()
        sEtaiTD.reset()
        sVoltTD.reset()
        sAgrTD.reset()
    elif plot==5:
        sCdTD.reset() #Sliders for T/D
        sAltTD.reset()
        sSolTD.reset()
        sEtaiTD.reset()
        sVoltTD.reset()
        sAgrTD.reset()
    
buttonReset.on_clicked(reset)
plt.show()

#====Save PNG Button ======
savepngax = plt.axes([0.05, 0.9, 0.15, 0.04]) #button configuration
buttonSavePng = Button(savepngax, 'Save PNG', color=axcolor, hovercolor='0.975')

def savePng(event): #save data
    if plot==1:
        plt.savefig("drag_plot.png")
        
    elif plot==2:
        plt.savefig("AO_plot.png")
        
    elif plot==3:
        plt.savefig("decay_plot.png")
        
    elif plot==4:
        plt.savefig("TD_plot.png")
    
    elif plot==5:
        plt.savefig("TD_etai_plot.png")

buttonSavePng.on_clicked(savePng)
plt.show()


#====Save CSV Button ======
saveax = plt.axes([0.05, 0.95, 0.15, 0.04]) #button configuration
buttonSaveCSV = Button(saveax, 'Save CSV', color=axcolor, hovercolor='0.975')

def saveCsv(event): #save data
    if plot==1:
        with open('drag_results.csv', mode='w') as results: #Save data for Drag plot
            writer = csv.writer(results, delimiter=',',lineterminator = '\n', quoting=csv.QUOTE_ALL)
            
            if Ar_classic == 0:
                writer.writerow(["Drag [N]","Thrust [N]", "Altitude [km]", "Cd [-]", "eta z", "Solar act."])        
                for i in range (0,len(yD)):
                    if i==0:
                        writer.writerow([xDoutput[0][i],xDoutput[1][i], yDoutput[i], CdOutput , etazOutput, solarOutput])
                    else:
                        writer.writerow([xDoutput[0][i],xDoutput[1][i], yDoutput[i]])
            elif Ar_classic ==1:
                writer.writerow(["Drag 3U [N]","Drag 6U [N]","Drag 12U [N]","Drag 27U [N]","Thrust [N]", "Altitude [km]", "Cd [-]", "eta z", "Solar act."])        
                for i in range (0,len(yD)):
                    if i==0:
                        writer.writerow([xDoutput[0][i],xDoutput[1][i],xDoutput[2][i],xDoutput[3][i],xDoutput[4][i], yD[i], CdoOtput, etazOuput, solarOutput])
                    else:
                        writer.writerow([xDoutput[0][i],xDoutput[1][i],xDoutput[2][i],xDoutput[3][i],xDoutput[4][i], yD[i]])
                
    elif plot==2:
        with open('AO_results.csv', mode='w') as results: #Save data for AO plot
            writer = csv.writer(results, delimiter=',',lineterminator = '\n', quoting=csv.QUOTE_ALL)
            writer.writerow(["AO amount [N/m2]", "Altitude [km]", "Time [days]", "Area Body [m2]", "Area Inlet [m2]", "Sol Flux"])
            for i in range (0,3) :
                writer.writerow([oxyglobal[i], aglobal, tglobal , areabodyglobal, areainletglobal ,labels[i]])

    elif plot==3:
        with open('decay_results.csv', mode='w') as results: #Save data for Decay plot
            writer = csv.writer(results, delimiter=',',lineterminator = '\n', quoting=csv.QUOTE_ALL)
            writer.writerow(["Days", "Altitude [km]", "Thrust [N]", "Ram Area [m2]", "Cd [-]","Solar act."])
            for i in range (0,len(xglobal)):
                if i==0:
                    writer.writerow([xglobal[i], yglobal[i], thrustGlobal, ramGlobal, CdOutput, solarOutput]) 
                else:
                    writer.writerow([xglobal[i], yglobal[i]]) 
                
    elif plot==4:
        with open('TD_results.csv', mode='w') as results: #Save data for TD plot
            writer = csv.writer(results, delimiter=',',lineterminator = '\n', quoting=csv.QUOTE_ALL)
            writer.writerow(["T/D ratio [-] 500 V","T/D ratio 1000 V [-]", "T/D ratio 1500 V [-]", "T/D custom ratio [-]","Drag [N]" , "Altitude [km]", "Grid radius [m]", "Grid Voltage [V]", "Cd [-]", "Solar act.", "eta z", "eta i"])
            for i in range (0,len(TDoutput)):
                if i==0:
                    writer.writerow([ TDvoloutput[0][i], TDvoloutput[1][i], TDvoloutput[2][i], TDoutput[i], Doutput[i], Altitudeoutput[i], gridRadiusOutput, gridVoltageOutput, CdOutput, solarOutput, etazOutput, etaiOutput])
                else:
                    writer.writerow([ TDvoloutput[0][i], TDvoloutput[1][i], TDvoloutput[2][i], TDoutput[i], Doutput[i], Altitudeoutput[i]])
                
    elif plot==5:
        with open('TD_etai_results.csv', mode='w') as results: #Save data for TD plot
            writer = csv.writer(results, delimiter=',',lineterminator = '\n', quoting=csv.QUOTE_ALL)
            if updated==0:
                writer.writerow(["T/D [-]", "Drag [N]", "Capture eff [-]", "Grid radius [m]", "Grid Voltage [V]", "Altitude [km]", "Cd [-]", "Solar act.", "Custom eta i"])
                for i in range (0,len(TDspecoutput)):
                    if i==0:
                        writer.writerow([TDspecoutput[i] ,Dspecoutput, Etazoutput[i], gridRadiusOutput, gridVoltageOutput, altiOutput, CdOutput, solarOutput, etaiOutput])
                    else:
                        writer.writerow([TDspecoutput[i] ,Dspecoutput, Etazoutput[i]])
                    

            elif updated==1:
                writer.writerow(["T/D etai 2 [N]","T/D etai 3 [N]","T/D etai 4 [N]","T/D etai 5 [N]","T/D etai 6 [N]","T/D etai 7 [N]","T/D etai 8 [N]","T/D etai 9 [N]","T/D etai 10 [N]","T/D custom etai","Drag [N]" , "Capture eff [-]", "Grid radius [m]", "Grid Voltage [V]", "Altitude [km]", "Cd [-]", "Solar act.", "Custom eta i"])
                for i in range (0,len(TDArroutput[0])):
                    if i==0:
                        writer.writerow([TDArroutput[0][i],TDArroutput[1][i],TDArroutput[2][i],TDArroutput[3][i],TDArroutput[4][i],TDArroutput[5][i],TDArroutput[6][i],TDArroutput[7][i],TDArroutput[8][i],TDspecoutput[i] ,Dspecoutput, Etazoutput[i], gridRadiusOutput, gridVoltageOutput, altiOutput, CdOutput, solarOutput, etaiOutput])
                    else:
                        writer.writerow([TDArroutput[0][i],TDArroutput[1][i],TDArroutput[2][i],TDArroutput[3][i],TDArroutput[4][i],TDArroutput[5][i],TDArroutput[6][i],TDArroutput[7][i],TDArroutput[8][i],TDspecoutput[i] ,Dspecoutput, Etazoutput[i]])

buttonSaveCSV.on_clicked(saveCsv)
plt.show()

       


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [16]:
yOMeter=get_decay_data_minutes(2.2,0.1,0,400,92)[0] #new values of x/y
xOMin=get_decay_data_minutes(2.2,0.1,0,400,92)[1]

In [50]:
plot =3